In [1]:
# 
#    These are standard python modules
#
#import json, time, urllib.parse
import json, time
#
#    The 'requests' module is a distribution module for making web requests.
#
import requests

In [2]:
#########
#
#    CONSTANTS
#

#
#    This is the root of all AQS API URLs
#
API_REQUEST_URL = 'https://aqs.epa.gov/data/api'

#
#    These are 'actions' we can ask the API to take or requests that we can make of the API
#
#    Sign-up request - generally only performed once - unless you lose your key
API_ACTION_SIGNUP = '/signup?email={email}'
#
#    List actions provide information on API parameter values that are required by some other actions/requests
API_ACTION_LIST_CLASSES = '/list/classes?email={email}&key={key}'
API_ACTION_LIST_PARAMS = '/list/parametersByClass?email={email}&key={key}&pc={pclass}'
API_ACTION_LIST_SITES = '/list/sitesByCounty?email={email}&key={key}&state={state}&county={county}'
#
#    Monitor actions are requests for monitoring stations that meet specific criteria
API_ACTION_MONITORS_COUNTY = '/monitors/byCounty?email={email}&key={key}&param={param}&bdate={begin_date}&edate={end_date}&state={state}&county={county}'
API_ACTION_MONITORS_BOX = '/monitors/byBox?email={email}&key={key}&param={param}&bdate={begin_date}&edate={end_date}&minlat={minlat}&maxlat={maxlat}&minlon={minlon}&maxlon={maxlon}'
#
#    Summary actions are requests for summary data. These are for daily summaries
API_ACTION_DAILY_SUMMARY_COUNTY = '/dailyData/byCounty?email={email}&key={key}&param={param}&bdate={begin_date}&edate={end_date}&state={state}&county={county}'
API_ACTION_DAILY_SUMMARY_BOX = '/dailyData/byBox?email={email}&key={key}&param={param}&bdate={begin_date}&edate={end_date}&minlat={minlat}&maxlat={maxlat}&minlon={minlon}&maxlon={maxlon}'
#
#    It is always nice to be respectful of a free data resource.
#    We're going to observe a 100 requests per minute limit - which is fairly nice
API_LATENCY_ASSUMED = 0.002       # Assuming roughly 2ms latency on the API and network
API_THROTTLE_WAIT = (1.0/100.0)-API_LATENCY_ASSUMED
#
#
#    This is a template that covers most of the parameters for the actions we might take, from the set of actions
#    above. In the examples below, most of the time parameters can either be supplied as individual values to a
#    function - or they can be set in a copy of the template and passed in with the template.
# 
AQS_REQUEST_TEMPLATE = {
    "email":      "",     
    "key":        "",      
    "state":      "",     # the two digit state FIPS # as a string
    "county":     "",     # the three digit county FIPS # as a string
    "begin_date": "",     # the start of a time window in YYYYMMDD format
    "end_date":   "",     # the end of a time window in YYYYMMDD format, begin_date and end_date must be in the same year
    "minlat":    0.0,
    "maxlat":    0.0,
    "minlon":    0.0,
    "maxlon":    0.0,
    "param":     "",     # a list of comma separated 5 digit codes, max 5 codes requested
    "pclass":    ""      # parameter class is only used by the List calls
}



Making a sign up request

In [3]:
#
#    This implements the sign-up request. The parameters are standardized so that this function definition matches
#    all of the others. However, the easiest way to call this is to simply call this function with your preferred
#    email address.
#
def request_signup(email_address = None,
                   endpoint_url = API_REQUEST_URL, 
                   endpoint_action = API_ACTION_SIGNUP, 
                   request_template = AQS_REQUEST_TEMPLATE,
                   headers = None):
    
    # Make sure we have a string - if you don't have access to this email addres, things might go badly for you
    if email_address:
        request_template['email'] = email_address        
    if not request_template['email']: 
        raise Exception("Must supply an email address to call 'request_signup()'")
    
    # Compose the signup url - create a request URL by combining the endpoint_url with the parameters for the request
    request_url = endpoint_url+endpoint_action.format(**request_template)
        
    # make the request
    try:
        # Wait first, to make sure we don't exceed a rate limit in the situation where an exception occurs
        # during the request processing - throttling is always a good practice with a free data source
        if API_THROTTLE_WAIT > 0.0:
            time.sleep(API_THROTTLE_WAIT)
        response = requests.get(request_url, headers=headers)
        json_response = response.json()
    except Exception as e:
        print(e)
        json_response = None
    return json_response

In [ ]:
#
#    A SIGNUP request is only to be done once, to request a key. A key is sent to that email address and needs to be confirmed with a click through
#    This code should probably be commented out after you've made your key request to make sure you don't accidentally make a new sign-up request
#
#print("Requesting SIGNUP ...")
#response = request_signup("mdn27@uw.edu")
#print(json.dumps(response,indent=4))
#

In [6]:
#
#   Once we have the signup email, we can define two constants
#   USERNAME - This should be the email address you sent the EPA asking for access to the API during sign-up
#   APIKEY   - This should be the authorization key they sent you
#
#   In this case I don't want to distribute my keys with the source of the notebook, so I wrote a key manager object that
#   helps track all of my API keys - a username and domain name retrieves the key. The key manager hides the keys on disk
#   separate from the code. Often you see code that assumes you have stored your API key as an OS environment variable.
#
#from apikeys.Manager import Manager
#keyman = Manager()

USERNAME = "mdn27@uw.edu"
#key_info = keyman.findRecord(USERNAME,API_REQUEST_URL)
#APIKEY = key_info[0]['key']
APIKEY= 'greenosprey68' 
#print(key_info[0]['description'])
#print(APIKEY)
#
#   You can specify these as constants for your own use - just don't distribute the notebook without removing the constants
#
#USERNAME = "<the_email_address_you_sent_on_signup>"
#APIKEY = "<the_key_the_EPA_sent_you_in_email>"


# Making a list request

In [4]:
#
#    This implements the list request. There are several versions of the list request that only require email and key.
#    This code sets the default action/requests to list the groups or parameter class descriptors. Having those descriptors 
#    allows one to request the individual (proprietary) 5 digit codes for individual air quality measures by using the
#    param request. Some code in later cells will illustrate those requests.
#
def request_list_info(email_address = None, key = None,
                      endpoint_url = API_REQUEST_URL, 
                      endpoint_action = API_ACTION_LIST_CLASSES, 
                      request_template = AQS_REQUEST_TEMPLATE,
                      headers = None):
    
    #  Make sure we have email and key - at least
    #  This prioritizes the info from the call parameters - not what's already in the template
    if email_address:
        request_template['email'] = email_address
    if key:
        request_template['key'] = key
    
    # For the basic request we need an email address and a key
    if not request_template['email']:
        raise Exception("Must supply an email address to call 'request_list_info()'")
    if not request_template['key']: 
        raise Exception("Must supply a key to call 'request_list_info()'")

    # compose the request
    request_url = endpoint_url+endpoint_action.format(**request_template)
        
    # make the request
    try:
        # Wait first, to make sure we don't exceed a rate limit in the situation where an exception occurs
        # during the request processing - throttling is always a good practice with a free data source
        if API_THROTTLE_WAIT > 0.0:
            time.sleep(API_THROTTLE_WAIT)
        response = requests.get(request_url, headers=headers)
        json_response = response.json()
    except Exception as e:
        print(e)
        json_response = None
    return json_response



In [7]:
#
#   The default should get us a list of the various groups or classes of sensors. These classes are user defined names for clustors of
#   sensors that might be part of a package or default air quality sensing station. We need a class name to start getting down to the
#   a sensor ID. Each sensor type has an ID number. We'll eventually need those ID numbers to be able to request values that come from
#   that specific sensor.
#
request_data = AQS_REQUEST_TEMPLATE.copy()
request_data['email'] = USERNAME
request_data['key'] = APIKEY

response = request_list_info(request_template=request_data)

if response["Header"][0]['status'] == "Success":
    print(json.dumps(response['Data'],indent=4))
else:
    print(json.dumps(response,indent=4))


[
    {
        "code": "AIRNOW MAPS",
        "value_represented": "The parameters represented on AirNow maps (88101, 88502, and 44201)"
    },
    {
        "code": "ALL",
        "value_represented": "Select all Parameters Available"
    },
    {
        "code": "AQI POLLUTANTS",
        "value_represented": "Pollutants that have an AQI Defined"
    },
    {
        "code": "CORE_HAPS",
        "value_represented": "Urban Air Toxic Pollutants"
    },
    {
        "code": "CRITERIA",
        "value_represented": "Criteria Pollutants"
    },
    {
        "code": "CSN DART",
        "value_represented": "List of CSN speciation parameters to populate the STI DART tool"
    },
    {
        "code": "FORECAST",
        "value_represented": "Parameters routinely extracted by AirNow (STI)"
    },
    {
        "code": "HAPS",
        "value_represented": "Hazardous Air Pollutants"
    },
    {
        "code": "IMPROVE CARBON",
        "value_represented": "IMPROVE Carbon Parameters"
    }

In [8]:
#
#   Once we have a list of the classes or groups of possible sensors, we can find the sensor IDs that make up that class (group)
#   The one that looks to be associated with the Air Quality Index is "AQI POLLUTANTS"
#   We'll use that to make another list request.
#
AQI_PARAM_CLASS = "AQI POLLUTANTS"


In [9]:
#
#   Structure a request to get the sensor IDs associated with the AQI
#
request_data = AQS_REQUEST_TEMPLATE.copy()
request_data['email'] = USERNAME
request_data['key'] = APIKEY
request_data['pclass'] = AQI_PARAM_CLASS  # here we specify that we want this 'pclass' or parameter classs

response = request_list_info(request_template=request_data, endpoint_action=API_ACTION_LIST_PARAMS)

if response["Header"][0]['status'] == "Success":
    print(json.dumps(response['Data'],indent=4))
else:
    print(json.dumps(response,indent=4))


[
    {
        "code": "42101",
        "value_represented": "Carbon monoxide"
    },
    {
        "code": "42401",
        "value_represented": "Sulfur dioxide"
    },
    {
        "code": "42602",
        "value_represented": "Nitrogen dioxide (NO2)"
    },
    {
        "code": "44201",
        "value_represented": "Ozone"
    },
    {
        "code": "81102",
        "value_represented": "PM10 Total 0-10um STP"
    },
    {
        "code": "88101",
        "value_represented": "PM2.5 - Local Conditions"
    },
    {
        "code": "88502",
        "value_represented": "Acceptable PM2.5 AQI & Speciation Mass"
    }
]


In [10]:
#
#   Given the set of sensor codes, now we can create a parameter list or 'param' value as defined by the AQS API spec.
#   It turns out that we want all of these measures for AQI, but we need to have two different param constants to get
#   all seven of the code types. We can only have a max of 5 sensors/values request per param.
#
#   Gaseous AQI pollutants CO, SO2, NO2, and O2
AQI_PARAMS_GASEOUS = "42101,42401,42602,44201"
#
#   Particulate AQI pollutants PM10, PM2.5, and Acceptable PM2.5
AQI_PARAMS_PARTICULATES = "81102,88101,88502"
#   
#

In [11]:
#
#   We'll use these two city locations in the examples below.
#
CITY_LOCATIONS = {
    'West Odessa' :       {'city'   : 'West Odessa',
                       'county' : 'Ector',
                       'state'  : 'Texas',
                       'fips'   : '48135',
                       'latlon' : [31.8456, -102.3676] }
}


In [12]:
#
#  This list request should give us a list of all the monitoring stations in the county specified by the
#  given city selected from the CITY_LOCATIONS dictionary
#
request_data = AQS_REQUEST_TEMPLATE.copy()
request_data['email'] = USERNAME
request_data['key'] = APIKEY
request_data['state'] = CITY_LOCATIONS['West Odessa']['fips'][:2]   # the first two digits (characters) of FIPS is the state code
request_data['county'] = CITY_LOCATIONS['West Odessa']['fips'][2:]  # the last three digits (characters) of FIPS is the county code

response = request_list_info(request_template=request_data, endpoint_action=API_ACTION_LIST_SITES)

if response["Header"][0]['status'] == "Success":
    print(json.dumps(response['Data'],indent=4))
else:
    print(json.dumps(response,indent=4))


[
    {
        "code": "0001",
        "value_represented": null
    },
    {
        "code": "0002",
        "value_represented": null
    },
    {
        "code": "0003",
        "value_represented": "Odessa-Hays Elementary School"
    },
    {
        "code": "0004",
        "value_represented": "NW OF SAN BENITO AND S. BANDERA AVE."
    },
    {
        "code": "1014",
        "value_represented": "Odessa Gonzales"
    }
]


# Making Daily Summary Request

In [13]:
#
#    This implements the daily summary request. Daily summary provides a daily summary value for each sensor being requested
#    from the start date to the end date. 
#
#    Like the two other functions, this can be called with a mixture of a defined parameter dictionary, or with function
#    parameters. If function parameters are provided, those take precedence over any parameters from the request template.
#
def request_daily_summary(email_address = None, key = None, param=None,
                          begin_date = None, end_date = None, fips = None,
                          endpoint_url = API_REQUEST_URL, 
                          endpoint_action = API_ACTION_DAILY_SUMMARY_COUNTY, 
                          request_template = AQS_REQUEST_TEMPLATE,
                          headers = None):
    
    #  This prioritizes the info from the call parameters - not what's already in the template
    if email_address:
        request_template['email'] = email_address
    if key:
        request_template['key'] = key
    if param:
        request_template['param'] = param
    if begin_date:
        request_template['begin_date'] = begin_date
    if end_date:
        request_template['end_date'] = end_date
    if fips and len(fips)==5:
        request_template['state'] = fips[:2]
        request_template['county'] = fips[2:]            

    # Make sure there are values that allow us to make a call - these are always required
    if not request_template['email']:
        raise Exception("Must supply an email address to call 'request_daily_summary()'")
    if not request_template['key']: 
        raise Exception("Must supply a key to call 'request_daily_summary()'")
    if not request_template['param']: 
        raise Exception("Must supply param values to call 'request_daily_summary()'")
    if not request_template['begin_date']: 
        raise Exception("Must supply a begin_date to call 'request_daily_summary()'")
    if not request_template['end_date']: 
        raise Exception("Must supply an end_date to call 'request_daily_summary()'")
    # Note we're not validating FIPS fields because not all of the daily summary actions require the FIPS numbers
        
    # compose the request
    request_url = endpoint_url+endpoint_action.format(**request_template)
        
    # make the request
    try:
        # Wait first, to make sure we don't exceed a rate limit in the situation where an exception occurs
        # during the request processing - throttling is always a good practice with a free data source
        if API_THROTTLE_WAIT > 0.0:
            time.sleep(API_THROTTLE_WAIT)
        response = requests.get(request_url, headers=headers)
        json_response = response.json()
    except Exception as e:
        print(e)
        json_response = None
    return json_response



In [ ]:
'''
request_data = AQS_REQUEST_TEMPLATE.copy()
request_data['email'] = USERNAME
request_data['key'] = APIKEY
request_data['param'] = AQI_PARAMS_GASEOUS
request_data['state'] = CITY_LOCATIONS['West Odessa']['fips'][:2]
request_data['county'] = CITY_LOCATIONS['West Odessa']['fips'][2:]

# request daily summary data for the month of July in 2021
gaseous_aqi = request_daily_summary(request_template=request_data, begin_date="20210701", end_date="20210731")
print("Response for the gaseous pollutants ...")
#
if gaseous_aqi["Header"][0]['status'] == "Success":
    print(json.dumps(gaseous_aqi['Data'],indent=4))
elif gaseous_aqi["Header"][0]['status'].startswith("No data "):
    print("Looks like the response generated no data. You might take a closer look at your request and the response data.")
else:
    print(json.dumps(gaseous_aqi,indent=4))

request_data['param'] = AQI_PARAMS_PARTICULATES
# request daily summary data for the month of July in 2021
particulate_aqi = request_daily_summary(request_template=request_data, begin_date="20210701", end_date="20210731")
print("Response for the particulate pollutants ...")
#
if particulate_aqi["Header"][0]['status'] == "Success":
    print(json.dumps(particulate_aqi['Data'],indent=4))
elif particulate_aqi["Header"][0]['status'].startswith("No data "):
    print("Looks like the response generated no data. You might take a closer look at your request and the response data.")
else:
    print(json.dumps(particulate_aqi,indent=4))
'''

In [14]:
#
#    This is a list of field names - data - that will be extracted from each record
#
EXTRACTION_FIELDS = ['sample_duration','observation_count','arithmetic_mean','aqi']

#
#    The function creates a summary record
def extract_summary_from_response(r=None, fields=EXTRACTION_FIELDS):
    ## the result will be structured around monitoring site, parameter, and then date
    result = dict()
    data = r["Data"]
    for record in data:
        # make sure the record is set up
        site = record['site_number']
        param = record['parameter_code']
        #date = record['date_local']    # this version keeps the respnse value YYYY-
        date = record['date_local'].replace('-','') # this puts it in YYYYMMDD format
        if site not in result:
            result[site] = dict()
            result[site]['local_site_name'] = record['local_site_name']
            result[site]['site_address'] = record['site_address']
            result[site]['state'] = record['state']
            result[site]['county'] = record['county']
            result[site]['city'] = record['city']
            result[site]['pollutant_type'] = dict()
        if param not in result[site]['pollutant_type']:
            result[site]['pollutant_type'][param] = dict()
            result[site]['pollutant_type'][param]['parameter_name'] = record['parameter']
            result[site]['pollutant_type'][param]['units_of_measure'] = record['units_of_measure']
            result[site]['pollutant_type'][param]['method'] = record['method']
            result[site]['pollutant_type'][param]['data'] = dict()
        if date not in result[site]['pollutant_type'][param]['data']:
            result[site]['pollutant_type'][param]['data'][date] = list()
        
        # now extract the specified fields
        extract = dict()
        for k in fields:
            if str(k) in record:
                extract[str(k)] = record[k]
            else:
                # this makes sure we always have the requested fields, even if
                # we have a missing value for a given day/month
                extract[str(k)] = None
        
        # add this extraction to the list for the day
        result[site]['pollutant_type'][param]['data'][date].append(extract)
    
    return result


In [ ]:

#extract_gaseous = extract_summary_from_response(gaseous_aqi)
#print("Summary of gaseous extraction ...")
#print(json.dumps(extract_gaseous,indent=4))

#extract_particulate = extract_summary_from_response(all_gaseous_data[0])
#print("Summary of particulate extraction ...")
#print(json.dumps(extract_particulate,indent=4))


In [16]:
request_data = AQS_REQUEST_TEMPLATE.copy()
request_data['email'] = USERNAME
request_data['key'] = APIKEY
request_data['param'] = AQI_PARAMS_PARTICULATES
request_data['state'] = CITY_LOCATIONS['West Odessa']['fips'][:2]
request_data['county'] = CITY_LOCATIONS['West Odessa']['fips'][2:]

# Initialize an empty list to store the results
all_particulate_data = []

# Define the request template and base URL
request_template = "YOUR_REQUEST_TEMPLATE_HERE"
base_url = "YOUR_BASE_URL_HERE"

# Define the years you want to retrieve data for
start_year = 1963
end_year = 2023

# Loop through the years and request daily summary data
for year in range(start_year, end_year + 1):
    begin_date = f"{year}0101"
    end_date = f"{year}1231"

    # Make the request for the current year
    particulate_aqi = request_daily_summary(request_template=request_data, begin_date=begin_date, end_date=end_date)
    
    # Check the response and append data to the list
    if particulate_aqi["Header"][0]['status'] == "Success":
        #all_gaseous_data.extend(gaseous_aqi['Data'])
        extract_particulate = extract_summary_from_response(particulate_aqi)
        #print("Summary of particulate extraction ...")
        #print(json.dumps(extract_gaseous,indent=4))
        all_particulate_data.append(extract_particulate)
        
    elif particulate_aqi["Header"][0]['status'].startswith("No data "):
        print(f"No data available for {year}.")
        
    else:
        print(f"Error in retrieving data for {year}.")

# Print or process the collected data
print("Response for the particulate pollutants ...")
print(json.dumps(all_particulate_data, indent=4))

# Now, the all_gaseous_data list contains data for each year from 1963 to 2023.


No data available for 1963.
No data available for 1964.
No data available for 1965.
No data available for 1966.
No data available for 1967.
No data available for 1968.
No data available for 1969.
No data available for 1970.
No data available for 1971.
No data available for 1972.
No data available for 1973.
No data available for 1974.
No data available for 1975.
No data available for 1976.
No data available for 1977.
No data available for 1978.
No data available for 1979.
No data available for 1980.
No data available for 1981.
No data available for 1982.
No data available for 1983.
No data available for 1984.
No data available for 1992.
No data available for 1993.
No data available for 1994.
No data available for 1997.
No data available for 1998.
Response for the particulate pollutants ...


IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [17]:
# Define the output file name
output_file = "/Users/apple/Desktop/DATA_512/Project/data/particulate_data.json"

# Write the JSON data to the text file with an indentation of 4
with open(output_file, 'w') as file:
    json.dump(all_particulate_data, file, indent=4)

print(f"JSON data has been written to {output_file} with an indentation of 4.")

JSON data has been written to /Users/apple/Desktop/DATA_512/Project/data/particulate_data.json with an indentation of 4.


In [18]:
request_data = AQS_REQUEST_TEMPLATE.copy()
request_data['email'] = USERNAME
request_data['key'] = APIKEY
request_data['param'] = AQI_PARAMS_GASEOUS
request_data['state'] = CITY_LOCATIONS['West Odessa']['fips'][:2]
request_data['county'] = CITY_LOCATIONS['West Odessa']['fips'][2:]

# Initialize an empty list to store the results
all_gaseous_data = []

# Define the request template and base URL
request_template = "YOUR_REQUEST_TEMPLATE_HERE"
base_url = "YOUR_BASE_URL_HERE"

# Define the years you want to retrieve data for
start_year = 1963
end_year = 2023

# Loop through the years and request daily summary data
for year in range(start_year, end_year + 1):
    begin_date = f"{year}0101"
    end_date = f"{year}1231"

    # Make the request for the current year
    gaseous_aqi = request_daily_summary(request_template=request_data, begin_date=begin_date, end_date=end_date)
    
    # Check the response and append data to the list
    if gaseous_aqi["Header"][0]['status'] == "Success":
        #all_gaseous_data.extend(gaseous_aqi['Data'])
        extract_gaseous = extract_summary_from_response(gaseous_aqi)
        #print("Summary of particulate extraction ...")
        #print(json.dumps(extract_gaseous,indent=4))
        all_gaseous_data.append(extract_gaseous)
        
    elif gaseous_aqi["Header"][0]['status'].startswith("No data "):
        print(f"No data available for {year}.")
        
    else:
        print(f"Error in retrieving data for {year}.")

# Print or process the collected data
print("Response for the gaseous pollutants ...")
print(json.dumps(all_gaseous_data, indent=4))

# Now, the all_gaseous_data list contains data for each year from 1963 to 2023.


No data available for 1963.
No data available for 1964.
No data available for 1965.
No data available for 1966.
No data available for 1967.
No data available for 1968.
No data available for 1969.
No data available for 1970.
No data available for 1985.
No data available for 1987.
No data available for 1988.
No data available for 1989.
No data available for 1990.
No data available for 1991.
No data available for 1992.
No data available for 1993.
No data available for 1994.
No data available for 1995.
No data available for 1996.
No data available for 1997.
No data available for 1998.
No data available for 1999.
No data available for 2000.
No data available for 2001.
No data available for 2002.
No data available for 2003.
No data available for 2004.
No data available for 2005.
No data available for 2006.
No data available for 2007.
No data available for 2008.
No data available for 2009.
No data available for 2010.
No data available for 2011.
No data available for 2012.
No data available fo

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [19]:
# Define the output file name
output_file = "/Users/apple/Desktop/DATA_512/Project/data/gaseous_data.json"

# Write the JSON data to the text file with an indentation of 4
with open(output_file, 'w') as file:
    json.dump(all_gaseous_data, file, indent=4)

print(f"JSON data has been written to {output_file} with an indentation of 4.")

JSON data has been written to /Users/apple/Desktop/DATA_512/Project/data/gaseous_data.json with an indentation of 4.


In [74]:

# Initialize a list to store the extracted data
extracted_data = []

# Iterate through the list of datasets
for dataset in data:
    for key_1, value_1 in dataset.items():
        # Check if the dataset contains the relevant keys
        if "pollutant_type" in value_1 and isinstance(value_1["pollutant_type"], dict):
            for key_2, value_2 in value_1["pollutant_type"].items():
                if "data" in value_2 and isinstance(value_2["data"], dict):
                    for date, records in value_2["data"].items():
                        if isinstance(records, list):
                            for record in records:
                                print(date)
                                print(record)
                                break
                                #aqi = record.get("aqi")  # Use .get() to handle None values
                                aqi 
                                extracted_data.append({"date": date, "aqi": aqi})

# Print or further process the extracted data
#for entry in extracted_data:
    #print(f"Date: {entry['date']}, AQI: {entry['aqi']}")

19710521
{'sample_duration': '24 HOUR', 'observation_count': 1, 'arithmetic_mean': 4.9, 'aqi': None}
19710605
{'sample_duration': '24 HOUR', 'observation_count': 1, 'arithmetic_mean': 1.1, 'aqi': None}
19710609
{'sample_duration': '24 HOUR', 'observation_count': 1, 'arithmetic_mean': 1.1, 'aqi': None}
19710614
{'sample_duration': '24 HOUR', 'observation_count': 1, 'arithmetic_mean': 4.9, 'aqi': None}
19710619
{'sample_duration': '24 HOUR', 'observation_count': 1, 'arithmetic_mean': 1.1, 'aqi': None}
19710701
{'sample_duration': '24 HOUR', 'observation_count': 1, 'arithmetic_mean': 1.1, 'aqi': None}
19710825
{'sample_duration': '24 HOUR', 'observation_count': 1, 'arithmetic_mean': 1.1, 'aqi': None}
19710903
{'sample_duration': '24 HOUR', 'observation_count': 1, 'arithmetic_mean': 4.9, 'aqi': None}
19710911
{'sample_duration': '24 HOUR', 'observation_count': 1, 'arithmetic_mean': 1.1, 'aqi': None}
19710921
{'sample_duration': '24 HOUR', 'observation_count': 1, 'arithmetic_mean': 1.1, 'aq

In [80]:
def extract_aqi(data, dynamic_keys=None):
    if dynamic_keys is None:
        dynamic_keys = []

    extracted_data = []

    for key, value in data.items():
        current_keys = dynamic_keys + [key]

        if isinstance(value, dict):
            extracted_data.extend(extract_aqi(value, current_keys))
        elif isinstance(value, list):
            for item in value:
                if isinstance(item, dict):
                    aqi = item.get("aqi")
                    sample_duration = item.get("sample_duration")
                    if aqi is not None:
                        extracted_data.append({"keys": current_keys,"sample_duration": sample_duration, "aqi": aqi})

    return extracted_data

In [84]:
# Initialize a list to store the extracted data
extracted_data_gaseous = []

# Iterate through the list of datasets
for dataset in all_gaseous_data:
    extracted_data_gaseous.extend(extract_aqi(dataset))

# Print or further process the extracted data
for entry in extracted_data_gaseous:
    keys = " > ".join(entry["keys"])
    aqi = entry["aqi"]
    sample = entry['sample_duration']
    print(f"Keys: {keys}, AQI: {aqi} , SAMPLE: {sample}")

Keys: 0002 > pollutant_type > 42101 > data > 19760101, AQI: 5 , SAMPLE: 8-HR RUN AVG END HOUR
Keys: 0002 > pollutant_type > 42101 > data > 19760103, AQI: 15 , SAMPLE: 8-HR RUN AVG END HOUR
Keys: 0002 > pollutant_type > 42101 > data > 19760104, AQI: 2 , SAMPLE: 8-HR RUN AVG END HOUR
Keys: 0002 > pollutant_type > 42101 > data > 19760105, AQI: 6 , SAMPLE: 8-HR RUN AVG END HOUR
Keys: 0002 > pollutant_type > 42101 > data > 19760106, AQI: 9 , SAMPLE: 8-HR RUN AVG END HOUR
Keys: 0002 > pollutant_type > 42101 > data > 19760107, AQI: 9 , SAMPLE: 8-HR RUN AVG END HOUR
Keys: 0002 > pollutant_type > 42101 > data > 19760108, AQI: 9 , SAMPLE: 8-HR RUN AVG END HOUR
Keys: 0002 > pollutant_type > 42101 > data > 19760109, AQI: 5 , SAMPLE: 8-HR RUN AVG END HOUR
Keys: 0002 > pollutant_type > 42101 > data > 19760110, AQI: 7 , SAMPLE: 8-HR RUN AVG END HOUR
Keys: 0002 > pollutant_type > 42101 > data > 19760111, AQI: 11 , SAMPLE: 8-HR RUN AVG END HOUR
Keys: 0002 > pollutant_type > 42101 > data > 19760112, AQI

In [85]:
# Initialize a list to store the extracted data
extracted_data_particulate = []

# Iterate through the list of datasets
for dataset in all_particulate_data:
    extracted_data_particulate.extend(extract_aqi(dataset))

# Print or further process the extracted data
for entry in extracted_data_particulate:
    keys = " > ".join(entry["keys"])
    aqi = entry["aqi"]
    sample = entry['sample_duration']
    print(f"Keys: {keys}, AQI: {aqi} , SAMPLE: {sample}")

Keys: 0002 > pollutant_type > 81102 > data > 19850316, AQI: 16 , SAMPLE: 24 HOUR
Keys: 0002 > pollutant_type > 81102 > data > 19850318, AQI: 13 , SAMPLE: 24 HOUR
Keys: 0002 > pollutant_type > 81102 > data > 19850320, AQI: 25 , SAMPLE: 24 HOUR
Keys: 0002 > pollutant_type > 81102 > data > 19850322, AQI: 22 , SAMPLE: 24 HOUR
Keys: 0002 > pollutant_type > 81102 > data > 19850324, AQI: 19 , SAMPLE: 24 HOUR
Keys: 0002 > pollutant_type > 81102 > data > 19850326, AQI: 17 , SAMPLE: 24 HOUR
Keys: 0002 > pollutant_type > 81102 > data > 19850328, AQI: 24 , SAMPLE: 24 HOUR
Keys: 0002 > pollutant_type > 81102 > data > 19850330, AQI: 18 , SAMPLE: 24 HOUR
Keys: 0002 > pollutant_type > 81102 > data > 19850401, AQI: 24 , SAMPLE: 24 HOUR
Keys: 0002 > pollutant_type > 81102 > data > 19850405, AQI: 50 , SAMPLE: 24 HOUR
Keys: 0002 > pollutant_type > 81102 > data > 19850407, AQI: 39 , SAMPLE: 24 HOUR
Keys: 0002 > pollutant_type > 81102 > data > 19850409, AQI: 23 , SAMPLE: 24 HOUR
Keys: 0002 > pollutant_type 